In [1]:
from utils import *
import array 

from pydub import AudioSegment
import numba 
# %matplotlib inline

In [2]:
all_labels = [x[0].split('/')[-1] for x in os.walk("data/train/audio/")]
 


exclusions = ["","_background_noise_", "silence_many"]
POSSIBLE_LABELS = [item for item in all_labels if item not in exclusions]

In [3]:
# POSSIBLE_LABELS = 'yes no up down left right on off stop go silence unknown'.split()
id2name = {i: name for i, name in enumerate(POSSIBLE_LABELS)}
name2id = {name: i for i, name in id2name.items()}
len(id2name)

32

In [4]:
POSSIBLE_LABELS

['silence',
 'left',
 'eight',
 'no',
 'tree',
 'nine',
 'bed',
 'dog',
 'house',
 'cat',
 'bird',
 'four',
 'zero',
 'on',
 'right',
 'sheila',
 'train',
 'six',
 'seven',
 'down',
 'one',
 'go',
 'happy',
 'two',
 'yes',
 'up',
 'three',
 'five',
 'marvin',
 'stop',
 'wow',
 'off']

In [5]:
def load_data(data_dir):
    np.random.seed = 1
    
    """ Return 2 lists of tuples:
    [(class_id, user_id, path), ...] for train
    [(class_id, user_id, path), ...] for validation
    """
    # Just a simple regexp for paths with three groups:
    # prefix, label, user_id
#     pattern = re.compile("(.+\/)?(\w+)\/([^_]+)_.+wav")
    pattern  =  re.compile("(.+[\/\\\\])?(\w+)[\/\\\\]([^-]+)-.+wav")
    all_files = glob(os.path.join(data_dir, 'train/audio/*/*wav'))

    with open(os.path.join(data_dir, 'train/validation_list.txt'), 'r') as fin:
        validation_files = fin.readlines()
#     print validation_files
    valset = set()
    for entry in validation_files:
        r = re.match(pattern, entry.replace("_","-"))
        if r:
            valset.add(r.group(3))
    
    possible = set(POSSIBLE_LABELS)
    
    train, val, silent, unknown = [], [],[],[]
    
    for entry in all_files:
        r = re.match(pattern, entry)
        if r:
            label, uid = r.group(2), r.group(3)
            
            if label == '_background_noise_': #we've already split up noise files into 1 seg chunks under 'silence' folder
                continue
                
            if label not in possible:
                label = 'unknown'

            label_id = name2id[label]
            sample = (label, label_id, uid, entry)
            
            if uid in valset:    
                val.append(sample)
            elif label == "silence":
                silent.append(sample)
            elif label == "unknown":
                unknown.append(sample)                

            else:
                train.append(sample)

    print('There are {} train and {} val samples'.format(len(train), len(val)))
    
    columns_list = ['label', 'label_id', 'user_id', 'wav_file']
    

    train_df = pd.DataFrame(train, columns = columns_list)
    valid_df = pd.DataFrame(val, columns = columns_list)
    silent_df = pd.DataFrame(silent, columns = columns_list)
    unknown_df = pd.DataFrame(unknown, columns = columns_list)
    
    return train_df, valid_df, unknown_df, silent_df

In [6]:
train_df, valid_df, unknown_df, silent_df = load_data('./data/')

There are 57923 train and 6798 val samples


In [7]:
silent_df.head()

label  label_id   user_id  \
0  silence         0      dude   
1  silence         0   running   
2  silence         0     doing   
3  silence         0      pink   
4  silence         0  exercise   

                                            wav_file  
0  ./data/train/audio/silence/dude-miaowing14-rev...  
1  ./data/train/audio/silence/running-tap3-revers...  
2  ./data/train/audio/silence/doing-the-dishes85-...  
3        ./data/train/audio/silence/pink-noise16.wav  
4  ./data/train/audio/silence/exercise-bike192-re...

#### create validation dataframe

In [8]:
silent_df.label_id = name2id["silence"]


In [9]:
#augment validation set with silence and unknown files, made with step=250 when generating silence files
extra_data_size = 250 # int(valid_df.shape[0]*0.1)

# unknown_val = unknown_df.sample(extra_data_size,random_state=1)
# unknown_df = unknown_df[~unknown_df.index.isin(unknown_val.index.values)]

silent_val = silent_df.sample(extra_data_size,random_state=1)
silent_df = silent_df[~silent_df.index.isin(silent_val.index.values)]


valid_df = pd.concat([valid_df,silent_val],axis=0)

In [10]:
# silence_files = train_df[train_df.label == 'silence']
# train_df      = train_df[train_df.label != 'silence']

In [10]:
%%time

silence_files_AS = [AudioSegment.from_wav(x) for x in silent_df.wav_file.values]

filler = AudioSegment.silent(duration=1000, frame_rate = 16000)


CPU times: user 192 ms, sys: 80 ms, total: 272 ms
Wall time: 271 ms


In [16]:
train_df.label.value_counts().shape

(30,)

In [13]:
valid_df.label.value_counts()

four       280
no         270
down       264
seven      263
six        262
yes        261
go         260
zero       260
up         260
on         257
right      256
off        256
silence    250
three      248
left       247
stop       246
eight      243
five       242
two        236
nine       230
one        230
bed        197
happy      189
sheila     176
house      173
dog        170
cat        168
tree       166
wow        166
bird       162
marvin     160
Name: label, dtype: int64

### Feature extraction, augmentation, caching

In [12]:


def augment_wav(wav,pval=0.5):
    sample_rate = 16000
    L = 1000 #16000  # 1 sec
    
#     adjust speed, with 50% chance
#     wav = speed_change(wav,1.+ random.choice([.08,-0.08])) #random.uniform(-1, 1)*0.05) if np.random.random() < pval else wav
    
    
    #adjust volume
#     db_adjustment = random.uniform(-1, 1)*10
    wav = wav + random.choice([-8,-3,7,11]) #randodb_adjustment if np.random.random() < pval else wav
     
        
    #fill to 1 second
    wav = fill_to_1sec(wav)        
        
    #shift the audio by 10 ms
    shift_length = 120
    if np.random.random() < 0.5: #shift to left
        wav = wav[:L-shift_length]+ AudioSegment.silent(shift_length,frame_rate=sample_rate)
    else: #shift to right
        wav = AudioSegment.silent(shift_length,frame_rate=sample_rate) + wav[shift_length:]
        
        
        
    #blend original file with background noise     
#     if np.random.random() < pval:
    noise = random.choice(silence_files_AS)
    db_delta = (wav.dBFS - noise.dBFS) - random.choice([8,9,10])

    if db_delta< 0: #reduce intensity of loud background; if it's too silent, leave it be
        noise = noise  + db_delta
    wav = wav.overlay(noise)
 
    return wav

def log_mel(samples,sample_rate=16000,reshape=False,n_mels=256):

		S = librosa.feature.melspectrogram(samples, sr=sample_rate, n_mels=n_mels,hop_length=252)

		# Convert to log scale (dB). We'll use the peak power (max) as reference.
		log_S = librosa.power_to_db(S, ref=np.max)
		log_S = log_S.reshape(log_S.shape[0],-1,1) if reshape else log_S

		return 	log_S
    
def process_wav_file(record, reshape=False, augment=False,pval=0.5 ,output_format='logmel',n_mels=128 ):
    
    if type(record) == str: # test files
        fname = record
        label = "test"
    else:    
        fname  = record.wav_file
        label = record.label

        
        
        
        
    if "raw_AS_wav" in record: 
        wav = record.raw_AS_wav
    else:
        fname = fname.replace("\\","/")
        wav = AudioSegment.from_wav(fname.replace("_","-"))
        
        
    
    if (not label in ["silence"]) and augment: #no augmentation for sample files 
        wav = augment_wav(wav,pval)

    else: #make sure segment is 1 second
        wav = fill_to_1sec(wav)

        
    samples = AS_to_raw(wav)
    
    
    
    if output_format == "logmel":
        output = log_mel(samples,reshape=reshape,n_mels=n_mels)
        
    elif output_format == "mfcc":
        log_S = log_mel(samples,reshape=False,n_mels=n_mels)
        mfcc = librosa.feature.mfcc(S=log_S, n_mfcc=40) #hirese mfcc
        delta1 = librosa.feature.delta(mfcc, order=1)#hirese mfcc
        delta2 = librosa.feature.delta(mfcc, order=2)

        output = np.stack([mfcc,delta1,delta2])
        
    elif  output_format == "cqt":   
        samples = samples/samples
        output = librosa.cqt(samples, sr=16000 , fmin=librosa.note_to_hz('C2'),n_bins=60 * 2, bins_per_octave=12 * 2)
    else:
        output = samples
    
    
    return output


#### load existing datasets

In [15]:
# %%time 

# train_df = pickle.load( open("cache/train_df_waug.pik","rb"))
# valid_df = pickle.load( open("cache/valid_df.pik","rb"))
# silent_df = pickle.load(open("cache/silent_df.pik","rb"))
# unknown_df = pickle.load(open("cache/unknown_df_waug.pik","rb"))
# test_df =  pickle.load(open("cache/test_df.pik","rb"))

In [16]:
#ignore augmentations 
# train_df = train_df.iloc[:train_df.shape[0]/5]
# unknown_df = unknown_df.iloc[:unknown_df.shape[0]/5]

In [11]:
pickle.dump( train_df,open("cache/train_df_64_128_all_labels.pik","wb"),protocol=pickle.HIGHEST_PROTOCOL)
pickle.dump(valid_df, open("cache/valid_df_64_128_all_labels.pik","wb"),protocol=pickle.HIGHEST_PROTOCOL)
pickle.dump(silent_df, open("cache/silent_df_64_128.pik","wb"),protocol=pickle.HIGHEST_PROTOCOL)
# pickle.dump(unknown_df, open("cache/unknown_df.pik","wb"),protocol=pickle.HIGHEST_PROTOCOL)

### extract logmel 

In [14]:
%time valid_df["raw"]  = valid_df.wav_file.apply(lambda x : process_wav_file(x,augment=False,n_mels=256))
%time train_df["raw"]  = train_df.wav_file.apply(lambda x : process_wav_file(x,augment=False,n_mels=256))


CPU times: user 2min 43s, sys: 14 s, total: 2min 57s
Wall time: 1min 33s
CPU times: user 17min 56s, sys: 1min 30s, total: 19min 27s
Wall time: 10min 11s


In [15]:
pickle.dump(train_df,open("cache/train_df_all_labels.pik","wb"),protocol=pickle.HIGHEST_PROTOCOL)
pickle.dump(valid_df,open("cache/valid_df_all_labels.pik","wb"),protocol=pickle.HIGHEST_PROTOCOL)
# pickle.dump(silent_df, open("cache/silent_df_all_labels.pik","wb"),protocol=pickle.HIGHEST_PROTOCOL)
# pickle.dump(unknown_df, open("cache/unknown_df.pik","wb"),protocol=pickle.HIGHEST_PROTOCOL)

#### precompute augmentations 


In [21]:
#precomputing augs for faster neural net training
def precompute_augmentations(df,num_repeats=4):
    
    df_aug= pd.concat([df]*num_repeats)
    df_aug['raw'] = df_aug.wav_file.apply(lambda x :  process_wav_file(x,augment=True,n_mels=128))
    df = pd.concat([df, df_aug])
    
    return df 



In [20]:
# %time train_df = precompute_augmentations(train_df)

In [33]:
pickle.dump( train_df,open("cache/train_df_all_labels.pik","wb"),protocol=2)


### highres logmel (64x256)

In [14]:
import pandas as pd
import dask.dataframe as dd
from dask.multiprocessing import get

In [9]:
train_df["raw"] =train_df.wav_file.apply(lambda x:process_wav_file(x))

In [28]:
train_df.shape

(289615, 5)

In [23]:
%time train_df = precompute_augmentations(train_df)

CPU times: user 6h 43min 15s, sys: 20min 9s, total: 7h 3min 24s
Wall time: 23min 31s


In [32]:
train_df.dtypes

label       object
label_id     int64
user_id     object
wav_file    object
raw         object
dtype: object

In [24]:
pickle.dump( train_df,open("cache/train_df_all_labels_nospeed.pik","wb"),protocol=pickle.HIGHEST_PROTOCOL)


In [27]:
train_df.to_csv("cache/train_df_64x128_all_labels_nospeed.csv",index=False)

In [24]:
tdd = dd.from_pandas(train_df,npartitions=4)

In [15]:
valid_df_dd = dd.from_pandas(valid_df.head(), npartitions=4)

In [16]:

def process_frame(x):
        # process data frame
        return len(x) #process_wav_file(x,augment=False,n_mels=128)

In [ ]:
t = valid_df_dd.apply(lambda r: [process_wav_file(r.wav_file)] , axis=1,meta=('x', 'f8')).compute(get=get)  

Process ForkPoolWorker-1:
Process ForkPoolWorker-2:
Traceback (most recent call last):
  File "/home/ubuntu/anaconda2/envs/cx/lib/python3.6/multiprocessing/process.py", line 258, in _bootstrap
    self.run()
  File "/home/ubuntu/anaconda2/envs/cx/lib/python3.6/multiprocessing/process.py", line 93, in run
    self._target(*self._args, **self._kwargs)
Traceback (most recent call last):
  File "/home/ubuntu/anaconda2/envs/cx/lib/python3.6/multiprocessing/pool.py", line 103, in worker
    initializer(*initargs)
Process ForkPoolWorker-3:
  File "/home/ubuntu/anaconda2/envs/cx/lib/python3.6/multiprocessing/process.py", line 258, in _bootstrap
    self.run()
  File "/home/ubuntu/anaconda2/envs/cx/lib/python3.6/site-packages/dask/multiprocessing.py", line 192, in initialize_worker_process
    np.random.seed()
  File "/home/ubuntu/anaconda2/envs/cx/lib/python3.6/multiprocessing/process.py", line 93, in run
    self._target(*self._args, **self._kwargs)
TypeError: 'int' object is not callable
Tra

Traceback (most recent call last):
TypeError: 'int' object is not callable
  File "/home/ubuntu/anaconda2/envs/cx/lib/python3.6/site-packages/dask/multiprocessing.py", line 192, in initialize_worker_process
    np.random.seed()
  File "/home/ubuntu/anaconda2/envs/cx/lib/python3.6/multiprocessing/pool.py", line 103, in worker
    initializer(*initargs)
  File "/home/ubuntu/anaconda2/envs/cx/lib/python3.6/site-packages/dask/multiprocessing.py", line 192, in initialize_worker_process
    np.random.seed()
Process ForkPoolWorker-16:
  File "/home/ubuntu/anaconda2/envs/cx/lib/python3.6/multiprocessing/process.py", line 258, in _bootstrap
    self.run()
TypeError: 'int' object is not callable
TypeError: 'int' object is not callable
  File "/home/ubuntu/anaconda2/envs/cx/lib/python3.6/site-packages/dask/multiprocessing.py", line 192, in initialize_worker_process
    np.random.seed()
  File "/home/ubuntu/anaconda2/envs/cx/lib/python3.6/multiprocessing/process.py", line 93, in run
    self._targ

  File "/home/ubuntu/anaconda2/envs/cx/lib/python3.6/multiprocessing/process.py", line 258, in _bootstrap
    self.run()
TypeError: 'int' object is not callable
  File "/home/ubuntu/anaconda2/envs/cx/lib/python3.6/multiprocessing/pool.py", line 103, in worker
    initializer(*initargs)
  File "/home/ubuntu/anaconda2/envs/cx/lib/python3.6/multiprocessing/process.py", line 93, in run
    self._target(*self._args, **self._kwargs)
Traceback (most recent call last):
  File "/home/ubuntu/anaconda2/envs/cx/lib/python3.6/site-packages/dask/multiprocessing.py", line 192, in initialize_worker_process
    np.random.seed()
Process ForkPoolWorker-29:
  File "/home/ubuntu/anaconda2/envs/cx/lib/python3.6/multiprocessing/pool.py", line 103, in worker
    initializer(*initargs)
  File "/home/ubuntu/anaconda2/envs/cx/lib/python3.6/multiprocessing/process.py", line 258, in _bootstrap
    self.run()
TypeError: 'int' object is not callable
  File "/home/ubuntu/anaconda2/envs/cx/lib/python3.6/site-packages/

  File "/home/ubuntu/anaconda2/envs/cx/lib/python3.6/multiprocessing/process.py", line 93, in run
    self._target(*self._args, **self._kwargs)
Traceback (most recent call last):
Process ForkPoolWorker-41:
  File "/home/ubuntu/anaconda2/envs/cx/lib/python3.6/multiprocessing/pool.py", line 103, in worker
    initializer(*initargs)
  File "/home/ubuntu/anaconda2/envs/cx/lib/python3.6/multiprocessing/process.py", line 258, in _bootstrap
    self.run()
  File "/home/ubuntu/anaconda2/envs/cx/lib/python3.6/site-packages/dask/multiprocessing.py", line 192, in initialize_worker_process
    np.random.seed()
Traceback (most recent call last):
Process ForkPoolWorker-42:
  File "/home/ubuntu/anaconda2/envs/cx/lib/python3.6/multiprocessing/process.py", line 93, in run
    self._target(*self._args, **self._kwargs)
TypeError: 'int' object is not callable
  File "/home/ubuntu/anaconda2/envs/cx/lib/python3.6/multiprocessing/process.py", line 258, in _bootstrap
    self.run()
  File "/home/ubuntu/anacon

  File "/home/ubuntu/anaconda2/envs/cx/lib/python3.6/multiprocessing/process.py", line 93, in run
    self._target(*self._args, **self._kwargs)
  File "/home/ubuntu/anaconda2/envs/cx/lib/python3.6/site-packages/dask/multiprocessing.py", line 192, in initialize_worker_process
    np.random.seed()
  File "/home/ubuntu/anaconda2/envs/cx/lib/python3.6/multiprocessing/pool.py", line 103, in worker
    initializer(*initargs)
Traceback (most recent call last):
TypeError: 'int' object is not callable
  File "/home/ubuntu/anaconda2/envs/cx/lib/python3.6/site-packages/dask/multiprocessing.py", line 192, in initialize_worker_process
    np.random.seed()
  File "/home/ubuntu/anaconda2/envs/cx/lib/python3.6/multiprocessing/process.py", line 258, in _bootstrap
    self.run()
TypeError: 'int' object is not callable
Process ForkPoolWorker-54:
  File "/home/ubuntu/anaconda2/envs/cx/lib/python3.6/multiprocessing/process.py", line 93, in run
    self._target(*self._args, **self._kwargs)
  File "/home/ubu

...

TypeError: 'int' object is not callable
Process ForkPoolWorker-1581:
  File "/home/ubuntu/anaconda2/envs/cx/lib/python3.6/multiprocessing/process.py", line 258, in _bootstrap
    self.run()
Traceback (most recent call last):
Process ForkPoolWorker-1582:
  File "/home/ubuntu/anaconda2/envs/cx/lib/python3.6/multiprocessing/process.py", line 93, in run
    self._target(*self._args, **self._kwargs)
  File "/home/ubuntu/anaconda2/envs/cx/lib/python3.6/multiprocessing/pool.py", line 103, in worker
    initializer(*initargs)
Traceback (most recent call last):
Process ForkPoolWorker-1583:
  File "/home/ubuntu/anaconda2/envs/cx/lib/python3.6/multiprocessing/process.py", line 258, in _bootstrap
    self.run()
  File "/home/ubuntu/anaconda2/envs/cx/lib/python3.6/site-packages/dask/multiprocessing.py", line 192, in initialize_worker_process
    np.random.seed()
  File "/home/ubuntu/anaconda2/envs/cx/lib/python3.6/multiprocessing/process.py", line 93, in run
    self._target(*self._args, **self._kw

  File "/home/ubuntu/anaconda2/envs/cx/lib/python3.6/site-packages/dask/multiprocessing.py", line 192, in initialize_worker_process
    np.random.seed()
  File "/home/ubuntu/anaconda2/envs/cx/lib/python3.6/multiprocessing/pool.py", line 103, in worker
    initializer(*initargs)
Traceback (most recent call last):
  File "/home/ubuntu/anaconda2/envs/cx/lib/python3.6/multiprocessing/pool.py", line 103, in worker
    initializer(*initargs)
TypeError: 'int' object is not callable
Process ForkPoolWorker-1596:
  File "/home/ubuntu/anaconda2/envs/cx/lib/python3.6/site-packages/dask/multiprocessing.py", line 192, in initialize_worker_process
    np.random.seed()
  File "/home/ubuntu/anaconda2/envs/cx/lib/python3.6/multiprocessing/process.py", line 258, in _bootstrap
    self.run()
  File "/home/ubuntu/anaconda2/envs/cx/lib/python3.6/site-packages/dask/multiprocessing.py", line 192, in initialize_worker_process
    np.random.seed()
TypeError: 'int' object is not callable
  File "/home/ubuntu/ana

  File "/home/ubuntu/anaconda2/envs/cx/lib/python3.6/multiprocessing/pool.py", line 103, in worker
    initializer(*initargs)
Traceback (most recent call last):
  File "/home/ubuntu/anaconda2/envs/cx/lib/python3.6/site-packages/dask/multiprocessing.py", line 192, in initialize_worker_process
    np.random.seed()
Process ForkPoolWorker-1608:
TypeError: 'int' object is not callable
  File "/home/ubuntu/anaconda2/envs/cx/lib/python3.6/multiprocessing/process.py", line 258, in _bootstrap
    self.run()
  File "/home/ubuntu/anaconda2/envs/cx/lib/python3.6/multiprocessing/process.py", line 93, in run
    self._target(*self._args, **self._kwargs)
  File "/home/ubuntu/anaconda2/envs/cx/lib/python3.6/multiprocessing/pool.py", line 103, in worker
    initializer(*initargs)
Traceback (most recent call last):
Process ForkPoolWorker-1609:
  File "/home/ubuntu/anaconda2/envs/cx/lib/python3.6/site-packages/dask/multiprocessing.py", line 192, in initialize_worker_process
    np.random.seed()
  File "/

  File "/home/ubuntu/anaconda2/envs/cx/lib/python3.6/multiprocessing/process.py", line 93, in run
    self._target(*self._args, **self._kwargs)
TypeError: 'int' object is not callable
Traceback (most recent call last):
  File "/home/ubuntu/anaconda2/envs/cx/lib/python3.6/multiprocessing/pool.py", line 103, in worker
    initializer(*initargs)
  File "/home/ubuntu/anaconda2/envs/cx/lib/python3.6/multiprocessing/process.py", line 258, in _bootstrap
    self.run()
  File "/home/ubuntu/anaconda2/envs/cx/lib/python3.6/site-packages/dask/multiprocessing.py", line 192, in initialize_worker_process
    np.random.seed()
Process ForkPoolWorker-1621:
  File "/home/ubuntu/anaconda2/envs/cx/lib/python3.6/multiprocessing/process.py", line 93, in run
    self._target(*self._args, **self._kwargs)
TypeError: 'int' object is not callable
  File "/home/ubuntu/anaconda2/envs/cx/lib/python3.6/multiprocessing/pool.py", line 103, in worker
    initializer(*initargs)
  File "/home/ubuntu/anaconda2/envs/cx/lib

  File "/home/ubuntu/anaconda2/envs/cx/lib/python3.6/site-packages/dask/multiprocessing.py", line 192, in initialize_worker_process
    np.random.seed()
  File "/home/ubuntu/anaconda2/envs/cx/lib/python3.6/site-packages/dask/multiprocessing.py", line 192, in initialize_worker_process
    np.random.seed()
  File "/home/ubuntu/anaconda2/envs/cx/lib/python3.6/multiprocessing/pool.py", line 103, in worker
    initializer(*initargs)
  File "/home/ubuntu/anaconda2/envs/cx/lib/python3.6/multiprocessing/process.py", line 258, in _bootstrap
    self.run()
TypeError: 'int' object is not callable
TypeError: 'int' object is not callable
  File "/home/ubuntu/anaconda2/envs/cx/lib/python3.6/site-packages/dask/multiprocessing.py", line 192, in initialize_worker_process
    np.random.seed()
  File "/home/ubuntu/anaconda2/envs/cx/lib/python3.6/multiprocessing/process.py", line 93, in run
    self._target(*self._args, **self._kwargs)
TypeError: 'int' object is not callable
Traceback (most recent call la

In [23]:
res = valid_df_dd.head().map_partitions(lambda df: df.apply(process_frame) ,meta=('x', 'f8')).compute(get=get)  


AttributeError: 'DataFrame' object has no attribute 'map_partitions'

Process ForkPoolWorker-1885:
Traceback (most recent call last):
  File "/home/ubuntu/anaconda2/envs/cx/lib/python3.6/multiprocessing/process.py", line 258, in _bootstrap
    self.run()
  File "/home/ubuntu/anaconda2/envs/cx/lib/python3.6/multiprocessing/process.py", line 93, in run
    self._target(*self._args, **self._kwargs)
  File "/home/ubuntu/anaconda2/envs/cx/lib/python3.6/multiprocessing/pool.py", line 103, in worker
    initializer(*initargs)
  File "/home/ubuntu/anaconda2/envs/cx/lib/python3.6/site-packages/dask/multiprocessing.py", line 192, in initialize_worker_process
    np.random.seed()
TypeError: 'int' object is not callable
Process ForkPoolWorker-1886:
Traceback (most recent call last):
  File "/home/ubuntu/anaconda2/envs/cx/lib/python3.6/multiprocessing/process.py", line 258, in _bootstrap
    self.run()
  File "/home/ubuntu/anaconda2/envs/cx/lib/python3.6/multiprocessing/process.py", line 93, in run
    self._target(*self._args, **self._kwargs)
  File "/home/ubuntu/an

  File "/home/ubuntu/anaconda2/envs/cx/lib/python3.6/site-packages/dask/multiprocessing.py", line 192, in initialize_worker_process
    np.random.seed()
Traceback (most recent call last):
Process ForkPoolWorker-1899:
  File "/home/ubuntu/anaconda2/envs/cx/lib/python3.6/multiprocessing/process.py", line 258, in _bootstrap
    self.run()
TypeError: 'int' object is not callable
  File "/home/ubuntu/anaconda2/envs/cx/lib/python3.6/multiprocessing/process.py", line 93, in run
    self._target(*self._args, **self._kwargs)
  File "/home/ubuntu/anaconda2/envs/cx/lib/python3.6/multiprocessing/pool.py", line 103, in worker
    initializer(*initargs)
  File "/home/ubuntu/anaconda2/envs/cx/lib/python3.6/site-packages/dask/multiprocessing.py", line 192, in initialize_worker_process
    np.random.seed()
Traceback (most recent call last):
Process ForkPoolWorker-1900:
TypeError: 'int' object is not callable
  File "/home/ubuntu/anaconda2/envs/cx/lib/python3.6/multiprocessing/process.py", line 258, in 

  File "/home/ubuntu/anaconda2/envs/cx/lib/python3.6/multiprocessing/pool.py", line 103, in worker
    initializer(*initargs)
Traceback (most recent call last):
Process ForkPoolWorker-1912:
  File "/home/ubuntu/anaconda2/envs/cx/lib/python3.6/multiprocessing/process.py", line 258, in _bootstrap
    self.run()
  File "/home/ubuntu/anaconda2/envs/cx/lib/python3.6/site-packages/dask/multiprocessing.py", line 192, in initialize_worker_process
    np.random.seed()
  File "/home/ubuntu/anaconda2/envs/cx/lib/python3.6/multiprocessing/process.py", line 93, in run
    self._target(*self._args, **self._kwargs)
TypeError: 'int' object is not callable
  File "/home/ubuntu/anaconda2/envs/cx/lib/python3.6/multiprocessing/pool.py", line 103, in worker
    initializer(*initargs)
  File "/home/ubuntu/anaconda2/envs/cx/lib/python3.6/site-packages/dask/multiprocessing.py", line 192, in initialize_worker_process
    np.random.seed()
TypeError: 'int' object is not callable
Traceback (most recent call last)

TypeError: 'int' object is not callable
  File "/home/ubuntu/anaconda2/envs/cx/lib/python3.6/multiprocessing/process.py", line 93, in run
    self._target(*self._args, **self._kwargs)
  File "/home/ubuntu/anaconda2/envs/cx/lib/python3.6/multiprocessing/pool.py", line 103, in worker
    initializer(*initargs)
Traceback (most recent call last):
Process ForkPoolWorker-1925:
  File "/home/ubuntu/anaconda2/envs/cx/lib/python3.6/site-packages/dask/multiprocessing.py", line 192, in initialize_worker_process
    np.random.seed()
  File "/home/ubuntu/anaconda2/envs/cx/lib/python3.6/multiprocessing/process.py", line 258, in _bootstrap
    self.run()
TypeError: 'int' object is not callable
  File "/home/ubuntu/anaconda2/envs/cx/lib/python3.6/multiprocessing/process.py", line 93, in run
    self._target(*self._args, **self._kwargs)
  File "/home/ubuntu/anaconda2/envs/cx/lib/python3.6/multiprocessing/pool.py", line 103, in worker
    initializer(*initargs)
  File "/home/ubuntu/anaconda2/envs/cx/lib

...

  File "/home/ubuntu/anaconda2/envs/cx/lib/python3.6/site-packages/dask/multiprocessing.py", line 192, in initialize_worker_process
    np.random.seed()
TypeError: 'int' object is not callable
Traceback (most recent call last):
Process ForkPoolWorker-2498:
  File "/home/ubuntu/anaconda2/envs/cx/lib/python3.6/multiprocessing/process.py", line 258, in _bootstrap
    self.run()
  File "/home/ubuntu/anaconda2/envs/cx/lib/python3.6/multiprocessing/process.py", line 93, in run
    self._target(*self._args, **self._kwargs)
  File "/home/ubuntu/anaconda2/envs/cx/lib/python3.6/multiprocessing/pool.py", line 103, in worker
    initializer(*initargs)
  File "/home/ubuntu/anaconda2/envs/cx/lib/python3.6/site-packages/dask/multiprocessing.py", line 192, in initialize_worker_process
    np.random.seed()
TypeError: 'int' object is not callable
Traceback (most recent call last):
Process ForkPoolWorker-2499:
  File "/home/ubuntu/anaconda2/envs/cx/lib/python3.6/multiprocessing/process.py", line 258, in 

TypeError: 'int' object is not callable
  File "/home/ubuntu/anaconda2/envs/cx/lib/python3.6/multiprocessing/pool.py", line 103, in worker
    initializer(*initargs)
  File "/home/ubuntu/anaconda2/envs/cx/lib/python3.6/site-packages/dask/multiprocessing.py", line 192, in initialize_worker_process
    np.random.seed()
TypeError: 'int' object is not callable
Traceback (most recent call last):
Process ForkPoolWorker-2511:
  File "/home/ubuntu/anaconda2/envs/cx/lib/python3.6/multiprocessing/process.py", line 258, in _bootstrap
    self.run()
  File "/home/ubuntu/anaconda2/envs/cx/lib/python3.6/multiprocessing/process.py", line 93, in run
    self._target(*self._args, **self._kwargs)
  File "/home/ubuntu/anaconda2/envs/cx/lib/python3.6/multiprocessing/pool.py", line 103, in worker
    initializer(*initargs)
Traceback (most recent call last):
Process ForkPoolWorker-2512:
  File "/home/ubuntu/anaconda2/envs/cx/lib/python3.6/site-packages/dask/multiprocessing.py", line 192, in initialize_worke

  File "/home/ubuntu/anaconda2/envs/cx/lib/python3.6/multiprocessing/process.py", line 258, in _bootstrap
    self.run()
  File "/home/ubuntu/anaconda2/envs/cx/lib/python3.6/multiprocessing/process.py", line 93, in run
    self._target(*self._args, **self._kwargs)
  File "/home/ubuntu/anaconda2/envs/cx/lib/python3.6/multiprocessing/pool.py", line 103, in worker
    initializer(*initargs)
  File "/home/ubuntu/anaconda2/envs/cx/lib/python3.6/site-packages/dask/multiprocessing.py", line 192, in initialize_worker_process
    np.random.seed()
TypeError: 'int' object is not callable
Traceback (most recent call last):
Process ForkPoolWorker-2524:
  File "/home/ubuntu/anaconda2/envs/cx/lib/python3.6/multiprocessing/process.py", line 258, in _bootstrap
    self.run()
  File "/home/ubuntu/anaconda2/envs/cx/lib/python3.6/multiprocessing/process.py", line 93, in run
    self._target(*self._args, **self._kwargs)
  File "/home/ubuntu/anaconda2/envs/cx/lib/python3.6/multiprocessing/pool.py", line 103

  File "/home/ubuntu/anaconda2/envs/cx/lib/python3.6/multiprocessing/process.py", line 258, in _bootstrap
    self.run()
  File "/home/ubuntu/anaconda2/envs/cx/lib/python3.6/site-packages/dask/multiprocessing.py", line 192, in initialize_worker_process
    np.random.seed()
  File "/home/ubuntu/anaconda2/envs/cx/lib/python3.6/multiprocessing/process.py", line 93, in run
    self._target(*self._args, **self._kwargs)
TypeError: 'int' object is not callable
  File "/home/ubuntu/anaconda2/envs/cx/lib/python3.6/multiprocessing/pool.py", line 103, in worker
    initializer(*initargs)
  File "/home/ubuntu/anaconda2/envs/cx/lib/python3.6/site-packages/dask/multiprocessing.py", line 192, in initialize_worker_process
    np.random.seed()
TypeError: 'int' object is not callable
Traceback (most recent call last):
Process ForkPoolWorker-2537:
  File "/home/ubuntu/anaconda2/envs/cx/lib/python3.6/multiprocessing/process.py", line 258, in _bootstrap
    self.run()
  File "/home/ubuntu/anaconda2/envs/cx

Traceback (most recent call last):
Process ForkPoolWorker-2549:
  File "/home/ubuntu/anaconda2/envs/cx/lib/python3.6/multiprocessing/pool.py", line 103, in worker
    initializer(*initargs)
  File "/home/ubuntu/anaconda2/envs/cx/lib/python3.6/site-packages/dask/multiprocessing.py", line 192, in initialize_worker_process
    np.random.seed()
  File "/home/ubuntu/anaconda2/envs/cx/lib/python3.6/multiprocessing/process.py", line 258, in _bootstrap
    self.run()
TypeError: 'int' object is not callable
  File "/home/ubuntu/anaconda2/envs/cx/lib/python3.6/multiprocessing/process.py", line 93, in run
    self._target(*self._args, **self._kwargs)
  File "/home/ubuntu/anaconda2/envs/cx/lib/python3.6/multiprocessing/pool.py", line 103, in worker
    initializer(*initargs)
  File "/home/ubuntu/anaconda2/envs/cx/lib/python3.6/site-packages/dask/multiprocessing.py", line 192, in initialize_worker_process
    np.random.seed()
TypeError: 'int' object is not callable
Traceback (most recent call last)

In [ ]:
res = valid_df_dd.map_partitions(lambda df: df.wav_file.apply(process_frame) ,meta=('x', 'f8')).compute(get=get)  


In [21]:
# %time train_df["raw"]  = train_df.wav_file.apply(lambda x : process_wav_file(x,augment=False,n_mels=128))
%time train_df["raw"]  = tdd.map_partitions(lambda df: df.wav_file.apply(process_frame) ,meta=('x', 'f8')).compute(get=get)  

Process PoolWorker-1:
  File "/home/ubuntu/anaconda2/lib/python2.7/multiprocessing/process.py", line 267, in _bootstrap
Traceback (most recent call last):
    self.run()
  File "/home/ubuntu/anaconda2/lib/python2.7/multiprocessing/process.py", line 114, in run
    self._target(*self._args, **self._kwargs)
    initializer(*initargs)
Process PoolWorker-2:
  File "/home/ubuntu/anaconda2/lib/python2.7/multiprocessing/pool.py", line 97, in worker
Traceback (most recent call last):
  File "/home/ubuntu/anaconda2/lib/python2.7/multiprocessing/process.py", line 267, in _bootstrap
  File "/home/ubuntu/anaconda2/lib/python2.7/site-packages/dask/multiprocessing.py", line 192, in initialize_worker_process
    self.run()
    np.random.seed()
  File "/home/ubuntu/anaconda2/lib/python2.7/multiprocessing/process.py", line 114, in run
TypeError: 'int' object is not callable
    self._target(*self._args, **self._kwargs)
  File "/home/ubuntu/anaconda2/lib/python2.7/multiprocessing/pool.py", line 97, in w

  File "/home/ubuntu/anaconda2/lib/python2.7/multiprocessing/pool.py", line 97, in worker
    initializer(*initargs)
  File "/home/ubuntu/anaconda2/lib/python2.7/site-packages/dask/multiprocessing.py", line 192, in initialize_worker_process
    np.random.seed()
  File "/home/ubuntu/anaconda2/lib/python2.7/multiprocessing/process.py", line 267, in _bootstrap
Process PoolWorker-15:
TypeError: 'int' object is not callable
Traceback (most recent call last):
    self.run()
  File "/home/ubuntu/anaconda2/lib/python2.7/multiprocessing/process.py", line 114, in run
    self.run()
Process PoolWorker-16:
    self._target(*self._args, **self._kwargs)
Traceback (most recent call last):
  File "/home/ubuntu/anaconda2/lib/python2.7/multiprocessing/pool.py", line 97, in worker
  File "/home/ubuntu/anaconda2/lib/python2.7/multiprocessing/process.py", line 267, in _bootstrap
    initializer(*initargs)
  File "/home/ubuntu/anaconda2/lib/python2.7/site-packages/dask/multiprocessing.py", line 192, in init

    np.random.seed()
TypeError: 'int' object is not callable
Traceback (most recent call last):
  File "/home/ubuntu/anaconda2/lib/python2.7/multiprocessing/process.py", line 267, in _bootstrap
    self.run()
  File "/home/ubuntu/anaconda2/lib/python2.7/multiprocessing/process.py", line 114, in run
Process PoolWorker-29:
Traceback (most recent call last):
    self._target(*self._args, **self._kwargs)
  File "/home/ubuntu/anaconda2/lib/python2.7/multiprocessing/process.py", line 267, in _bootstrap
  File "/home/ubuntu/anaconda2/lib/python2.7/multiprocessing/pool.py", line 97, in worker
    self.run()
    initializer(*initargs)
  File "/home/ubuntu/anaconda2/lib/python2.7/multiprocessing/process.py", line 114, in run
  File "/home/ubuntu/anaconda2/lib/python2.7/site-packages/dask/multiprocessing.py", line 192, in initialize_worker_process
    self._target(*self._args, **self._kwargs)
Process PoolWorker-30:
    np.random.seed()
  File "/home/ubuntu/anaconda2/lib/python2.7/multiprocessing/

    self._target(*self._args, **self._kwargs)
  File "/home/ubuntu/anaconda2/lib/python2.7/multiprocessing/pool.py", line 97, in worker
    initializer(*initargs)
  File "/home/ubuntu/anaconda2/lib/python2.7/site-packages/dask/multiprocessing.py", line 192, in initialize_worker_process
    np.random.seed()
TypeError: 'int' object is not callable
Process PoolWorker-42:
Traceback (most recent call last):
  File "/home/ubuntu/anaconda2/lib/python2.7/multiprocessing/process.py", line 267, in _bootstrap
    self.run()
  File "/home/ubuntu/anaconda2/lib/python2.7/multiprocessing/process.py", line 114, in run
    self._target(*self._args, **self._kwargs)
  File "/home/ubuntu/anaconda2/lib/python2.7/multiprocessing/pool.py", line 97, in worker
    initializer(*initargs)
  File "/home/ubuntu/anaconda2/lib/python2.7/site-packages/dask/multiprocessing.py", line 192, in initialize_worker_process
    np.random.seed()
TypeError: 'int' object is not callable
Process PoolWorker-43:
Traceback (most rec

    np.random.seed()
TypeError: 'int' object is not callable
Process PoolWorker-55:
Traceback (most recent call last):
  File "/home/ubuntu/anaconda2/lib/python2.7/multiprocessing/process.py", line 267, in _bootstrap
    self.run()
  File "/home/ubuntu/anaconda2/lib/python2.7/multiprocessing/process.py", line 114, in run
    self._target(*self._args, **self._kwargs)
  File "/home/ubuntu/anaconda2/lib/python2.7/multiprocessing/pool.py", line 97, in worker
    initializer(*initargs)
  File "/home/ubuntu/anaconda2/lib/python2.7/site-packages/dask/multiprocessing.py", line 192, in initialize_worker_process
    np.random.seed()
TypeError: 'int' object is not callable
Process PoolWorker-56:
Traceback (most recent call last):
  File "/home/ubuntu/anaconda2/lib/python2.7/multiprocessing/process.py", line 267, in _bootstrap
    self.run()
  File "/home/ubuntu/anaconda2/lib/python2.7/multiprocessing/process.py", line 114, in run
    self._target(*self._args, **self._kwargs)
  File "/home/ubuntu/

...

  File "/home/ubuntu/anaconda2/lib/python2.7/site-packages/dask/multiprocessing.py", line 192, in initialize_worker_process
    np.random.seed()
TypeError: 'int' object is not callable
    np.random.seed()
Process PoolWorker-10357:
Traceback (most recent call last):
  File "/home/ubuntu/anaconda2/lib/python2.7/multiprocessing/process.py", line 267, in _bootstrap
TypeError: 'int' object is not callable
    self.run()
  File "/home/ubuntu/anaconda2/lib/python2.7/multiprocessing/process.py", line 114, in run
  File "/home/ubuntu/anaconda2/lib/python2.7/multiprocessing/pool.py", line 97, in worker
    self._target(*self._args, **self._kwargs)
  File "/home/ubuntu/anaconda2/lib/python2.7/multiprocessing/pool.py", line 97, in worker
    initializer(*initargs)
  File "/home/ubuntu/anaconda2/lib/python2.7/site-packages/dask/multiprocessing.py", line 192, in initialize_worker_process
    initializer(*initargs)
    np.random.seed()
  File "/home/ubuntu/anaconda2/lib/python2.7/multiprocessing/poo

Traceback (most recent call last):
  File "/home/ubuntu/anaconda2/lib/python2.7/multiprocessing/pool.py", line 97, in worker
    np.random.seed()
Process PoolWorker-10365:
    initializer(*initargs)
  File "/home/ubuntu/anaconda2/lib/python2.7/multiprocessing/process.py", line 267, in _bootstrap
TypeError: 'int' object is not callable
  File "/home/ubuntu/anaconda2/lib/python2.7/site-packages/dask/multiprocessing.py", line 192, in initialize_worker_process
Traceback (most recent call last):
    self.run()
  File "/home/ubuntu/anaconda2/lib/python2.7/multiprocessing/process.py", line 267, in _bootstrap
  File "/home/ubuntu/anaconda2/lib/python2.7/multiprocessing/process.py", line 114, in run
    np.random.seed()
    self._target(*self._args, **self._kwargs)
    self.run()
TypeError: 'int' object is not callable
  File "/home/ubuntu/anaconda2/lib/python2.7/multiprocessing/pool.py", line 97, in worker
  File "/home/ubuntu/anaconda2/lib/python2.7/multiprocessing/process.py", line 114, in r

    self.run()
    np.random.seed()
  File "/home/ubuntu/anaconda2/lib/python2.7/multiprocessing/process.py", line 114, in run
TypeError: 'int' object is not callable
    self._target(*self._args, **self._kwargs)
  File "/home/ubuntu/anaconda2/lib/python2.7/multiprocessing/pool.py", line 97, in worker
    initializer(*initargs)
  File "/home/ubuntu/anaconda2/lib/python2.7/site-packages/dask/multiprocessing.py", line 192, in initialize_worker_process
    np.random.seed()
Process PoolWorker-10375:
TypeError: 'int' object is not callable
Traceback (most recent call last):
  File "/home/ubuntu/anaconda2/lib/python2.7/multiprocessing/process.py", line 267, in _bootstrap
    self.run()
  File "/home/ubuntu/anaconda2/lib/python2.7/multiprocessing/process.py", line 114, in run
    self._target(*self._args, **self._kwargs)
  File "/home/ubuntu/anaconda2/lib/python2.7/multiprocessing/pool.py", line 97, in worker
    initializer(*initargs)
  File "/home/ubuntu/anaconda2/lib/python2.7/site-package

    self.run()
  File "/home/ubuntu/anaconda2/lib/python2.7/multiprocessing/process.py", line 114, in run
    initializer(*initargs)
  File "/home/ubuntu/anaconda2/lib/python2.7/site-packages/dask/multiprocessing.py", line 192, in initialize_worker_process
    np.random.seed()
TypeError: 'int' object is not callable
  File "/home/ubuntu/anaconda2/lib/python2.7/multiprocessing/process.py", line 114, in run
    np.random.seed()
Process PoolWorker-10391:
Traceback (most recent call last):
Process PoolWorker-10390:
    self._target(*self._args, **self._kwargs)
  File "/home/ubuntu/anaconda2/lib/python2.7/multiprocessing/process.py", line 267, in _bootstrap
  File "/home/ubuntu/anaconda2/lib/python2.7/multiprocessing/process.py", line 267, in _bootstrap
  File "/home/ubuntu/anaconda2/lib/python2.7/multiprocessing/pool.py", line 97, in worker
    self.run()
Traceback (most recent call last):
    self.run()
  File "/home/ubuntu/anaconda2/lib/python2.7/multiprocessing/process.py", line 267, in

    np.random.seed()
TypeError: 'int' object is not callable
  File "/home/ubuntu/anaconda2/lib/python2.7/site-packages/dask/multiprocessing.py", line 192, in initialize_worker_process
    np.random.seed()
TypeError: 'int' object is not callable
  File "/home/ubuntu/anaconda2/lib/python2.7/site-packages/dask/multiprocessing.py", line 192, in initialize_worker_process
    np.random.seed()
TypeError: 'int' object is not callable
Process PoolWorker-10381:
Traceback (most recent call last):
  File "/home/ubuntu/anaconda2/lib/python2.7/multiprocessing/process.py", line 267, in _bootstrap
    self.run()
  File "/home/ubuntu/anaconda2/lib/python2.7/multiprocessing/process.py", line 114, in run
    self._target(*self._args, **self._kwargs)
  File "/home/ubuntu/anaconda2/lib/python2.7/multiprocessing/pool.py", line 97, in worker
    initializer(*initargs)
  File "/home/ubuntu/anaconda2/lib/python2.7/site-packages/dask/multiprocessing.py", line 192, in initialize_worker_process
    np.random.see

In [26]:
train_df.iloc[0].wav_file

'./data/train/audio/left/b2e2773a-nohash-1.wav'

In [35]:
t = train_df.wav_file.iloc[:100].apply(lambda x : process_wav_file(x,augment=False,n_mels=128))

In [37]:
t.shape

(100,)

In [34]:
t.iloc[0].wav_file

'./data/train/audio/left/b2e2773a-nohash-1.wav'

In [22]:
t[0].shape

(128, 64)

In [13]:
train_df.head()

label  label_id   user_id                                       wav_file  \
0  left         1  cb8f8307  ./data/train/audio/left/cb8f8307_nohash_1.wav   
1  left         1  b7a0754f  ./data/train/audio/left/b7a0754f_nohash_2.wav   
2  left         1  0132a06d  ./data/train/audio/left/0132a06d_nohash_3.wav   
3  left         1  f92e49f3  ./data/train/audio/left/f92e49f3_nohash_4.wav   
4  left         1  88053e92  ./data/train/audio/left/88053e92_nohash_1.wav   

                                                 raw  
0  [[-80.0, -80.0, -80.0, -70.0291307552, -59.660...  
1  [[-80.0, -80.0, -80.0, -80.0, -80.0, -80.0, -8...  
2  [[-80.0, -80.0, -80.0, -80.0, -80.0, -80.0, -8...  
3  [[-80.0, -80.0, -80.0, -80.0, -80.0, -80.0, -8...  
4  [[-80.0, -80.0, -80.0, -80.0, -80.0, -80.0, -7...

In [14]:
pickle.dump( train_df,open("cache/full_train_64x256.pik","wb"),protocol=pickle.HIGHEST_PROTOCOL)


In [11]:
%time silent_df["raw"]  = silent_df.wav_file.apply(lambda x : process_wav_file(x,augment=False,n_mels=256))


CPU times: user 9.82 s, sys: 992 ms, total: 10.8 s
Wall time: 5.76 s


In [13]:
silent_df.label_id = name2id["silence"]

In [20]:
silent_df.head()

label  label_id  user_id  \
0  silence         0     dude   
1  silence         0    white   
2  silence         0  running   
3  silence         0    doing   
4  silence         0  running   

                                            wav_file  \
0      ./data/train/audio/silence/dude_miaowing9.wav   
1       ./data/train/audio/silence/white_noise30.wav   
2       ./data/train/audio/silence/running_tap21.wav   
3  ./data/train/audio/silence/doing_the_dishes48.wav   
4       ./data/train/audio/silence/running_tap23.wav   

                                                 raw  
0  [[-26.0479067409, -26.7304945747, -28.30017659...  
1  [[-11.0503711873, -9.50959155146, -8.474045789...  
2  [[-22.5951091259, -23.4727587309, -24.93214347...  
3  [[-32.6431128994, -33.5104849932, -36.48777917...  
4  [[-16.7817323916, -15.7638179299, -14.67852553...

In [21]:
pickle.dump( silent_df,open("cache/silent_df_64x256.pik","wb"),protocol=pickle.HIGHEST_PROTOCOL)
